In [1]:
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [2]:
import pandas
import sympy as Ω
import matplotlib.pyplot as plt
import numpy as np
from scipy.misc import derivative
import pickle
from tqdm import tqdm_notebook as tqdm

from dataclasses import dataclass

import scipy.sparse
import scipy.sparse.linalg

import functools

In [3]:
Ω.init_printing()

In [5]:
i, k = Ω.symbols('i k')
I, K = Ω.symbols('I K')
h_x, h_t = Ω.symbols('h_x h_t')
l, T, H, D = Ω.symbols('l T H D')

u = Ω.IndexedBase('u', shape=(I + 1, K + 1))

gamma = Ω.symbols('gamma')
gamma_val = D * h_t / h_x**2

## простейшая неявная повышенного порядка аппроксимации

In [10]:
eqs = [
    (u[k, i] - u[k - 1, i]) / h_t - D * (u[k, i + 1] - 2 * u[k, i] + u[k, i - 1]) / (h_x**2),
    (u[k, 1] - u[k, -1]) / (2 * h_x) - H * u[k, 0],
    (u[k, I+1] - u[k, I - 1]) / (2 * h_x) + H * u[k, I],
]
eqs[0] = (eqs[0] * h_t).expand().subs({gamma_val:gamma})
eqs

### $i=1,I-1$

In [15]:
(eqs[0]).collect([
    u[k, i-1],
    u[k, i],
    u[k, i+1],
    u[k-1, i-1],
    u[k-1, i],
    u[k-1, i+1],
])

### $i=0$

In [13]:
solution = Ω.solve(eqs[0].subs({i:0}), u[k, -1])[0]
(-eqs[1]*2*h_x*gamma).subs({u[k, -1]: solution}).expand().collect([
    u[k, 0],
    u[k, 1],
])
# (-eqs[1] * h_x * 2 * gamma_val).subs({u[k, -1]: solution}).expand().collect([
#     u[k, 0],
#     u[k, 1],
# ])

### $i=I$

In [14]:
solution = Ω.solve(eqs[0].subs({i:I}), u[k, I+1])[0]
(eqs[2] * 2 * h_x * gamma).subs({u[k, I+1]: solution}).expand().collect([
    u[k, I-1],
    u[k, I],
])
# (eqs[2] * 2 * h_x * gamma_val).subs({u[k, I+1]: solution}).expand().collect([
#     u[k, I-1],
#     u[k, I],
# ])

## КН повышенного порядка аппроксимации

In [19]:
eqs = [
    (u[k, i] - u[k - 1, i]) / h_t - D / 2 * (
      (u[k-1, i + 1] - 2 * u[k-1, i] + u[k-1, i - 1]) +
      (u[k, i + 1] - 2 * u[k, i] + u[k, i - 1])
    ) / (h_x**2),
    (u[k, 1] - u[k, -1]) / (2 * h_x) - H * u[k, 0],
    (u[k, I+1] - u[k, I - 1]) / (2 * h_x) + H * u[k, I],
]
eqs[0] = (eqs[0] * 2 * h_t).expand().subs({gamma_val:gamma})
eqs[1] = (eqs[1] * 2 * h_x).expand()
eqs[2] = (eqs[2] * 2 * h_x).expand()
eqs

### $i=1,I-1$

In [22]:
(eqs[0]).collect([
    u[k, i-1],
    u[k, i],
    u[k, i+1],
    u[k-1, i-1],
    u[k-1, i],
    u[k-1, i+1],
])

### $i=0$

In [23]:
(eqs[0]/2).subs({i:0}).subs({
    u[k, -1]: Ω.solve(eqs[1], u[k, -1])[0],
    u[k-1, -1]: Ω.solve(eqs[1], u[k, -1])[0].subs({k:k-1}),
}).expand().collect([
    u[k - 1, 0],
    u[k - 1, 1],
    u[k, 0],
    u[k, 1],
])

### $i=I$

In [24]:
(eqs[0]/2).subs({i:I}).subs({
    u[k, I+1]: Ω.solve(eqs[2], u[k, I+1])[0],
    u[k-1, I+1]: Ω.solve(eqs[2], u[k, I+1])[0].subs({k:k-1}),
}).expand().collect([
    u[k - 1, I],
    u[k - 1, I+1],
    u[k, I],
    u[k, I+1],
])